# <center>CS568:Deep Learning</center>  <center>Spring 2020</center> 

## Sentiment Analysis Using RNN
In this recitation, we will use RNN to classify the sentiment of a piece of text using Pytorch.

### Load dataset
Pytorch uses torchtext to preprocess raw text data. NLP projects require these steps for preprocessing:

+ Read the data from disk
+ Tokenize the text
+ Create a mapping from word to a unique integer
+ Convert the text into lists of integers
+ Load the data in whatever format your deep learning framework requires
+ Pad the text so that all the sequences are the same length, so you can process them in batch

**Torchtext** is a library that makes all the above processing much easier. 

**[Spacy](https://spacy.io/)** is a library that has been specifically built to take sentences in various languages and split them into different tokens.

how to tokenize the text using Torchtext and Spacy?

![alt text](1.png)

In [0]:
import torch
import random
from torchtext import data
seed = 1234
torch.manual_seed(seed)

text = data.Field(tokenize = 'spacy')
label = data.LabelField(dtype = torch.float)

Download IMDB dataset with using torchtext. The IMDb dataset consists of 50,000 movie reviews, each marked as being a positive or negative review. This code automatically download dataset with train and test splits. 

In [0]:
from torchtext import datasets

training_data, testing_data = datasets.IMDB.splits(text, label)
print('Number of training examples: ',len(training_data))
print('Number of testing examples: ', len(testing_data))

downloading aclImdb_v1.tar.gz


aclImdb_v1.tar.gz: 100%|██████████| 84.1M/84.1M [00:07<00:00, 10.8MB/s]


Number of training examples:  25000
Number of testing examples:  25000


In [0]:
print(vars(training_data.examples[0]))

{'text': ['Interesting', 'mix', 'of', 'comments', 'that', 'it', 'would', 'be', 'hard', 'to', 'add', 'anything', 'constructive', 'to', '.', 'However', ',', 'i', "'ll", 'try', '.', 'This', 'was', 'a', 'very', 'good', 'action', 'film', 'with', 'some', 'great', 'set', 'pieces', '.', 'You', "'ll", 'note', 'I', 'specified', 'the', 'genre', '.', 'I', 'did', "n't", 'snipe', 'about', 'the', 'lack', 'of', 'characterisation', ',', 'and', 'I', 'did', "n't", 'berate', 'the', 'acting', '.', 'Enjoy', 'if', 'for', 'what', 'it', 'is', 'people', ',', 'a', 'well', 'above', 'average', 'action', 'film', '.', 'I', 'could', 'go', 'on', 'but', 'I', "'ve", 'made', 'my', 'comment', '.'], 'label': 'pos'}


Create a validation set using .split() method. 

In [0]:
training_data, validation_data = training_data.split(random_state = random.seed(SEED), split_ratio = 0.7)
# split ratio to split training data into train and validation sets. By default, it splits them with 0.7 ratio. 
print('Number of training examples: ',len(training_data))
print('Number of validation examples: ',len(validation_data))
print('Number of testing examples: ',len(testing_data))

Number of training examples:  17500
Number of validation examples:  7500
Number of testing examples:  25000


Now we have to build a vocabulary. 

+ Computer cannot operate on strings, only numbers.
+ The index of each word is used to construct a one-hot vector. 

| Word   |      Index    |  One-hot vectors  |
|--------|:-------------:|------------------:|
| apple  |  0            |[1, 0, 0, 0, 0, 0] |
| orange |  1            |[0, 1, 0, 0, 0, 0] |
| king   |  2            |[0, 0, 1, 0, 0, 0] |
| queen  |  3            |[0, 0, 0, 1, 0, 0] |
| cat    |  4            |[0, 0, 0, 0, 1, 0] |
| dog    |  5            |[0, 0, 0, 0, 0, 1] |

+ The vocabulary of our dataset which consists of words and  their unique indexes $V = \{apple, orange, king, queen, cat, dog\}$
+ If we have 100,000 words in our vocabulary then one-hot vectors has 100,000 dimensions. 
+ This will make training slow and won't even fit into the memory of your computer.
+ The vocabulary can be cut down to take the top $n$  most common words.
+ Replace the words that do not appear in vocabulary with $<unk>$ token.
+ To ensure that each sentence in the batch has same size, pad the short sentences with $<pad>$ token. 

In [0]:
vocab_size = 25000
text.build_vocab(train_data, max_size = vocab_size)
label.build_vocab(train_data)
print('Unique tokens in text vocab: ',len(text.vocab))
print('Unique tokens in label vocab: ',len(label.vocab))

Unique tokens in TEXT vocabulary:  25002
Unique tokens in LABEL vocabulary:  2


Why is the vocab size 25002 and not 25000? One of the addition tokens is the < unk > token and the other is a < pad > token.
    
Torchtext has its own class called vocab for handling the vocabulary. The vocab class holds a mapping from word to id in its **stoi** attribute and a reverse mapping in its **itos** attribute. In addition to this, it can automatically build an embedding matrix for you using various pretrained embeddings like word2vec.

Print most common 10 words from the vocab. 

In [0]:
print(text.vocab.freqs.most_common(5))

[('the', 202286), (',', 192561), ('.', 165812), ('a', 109233), ('and', 109205)]


To view the vocab., use stoi (string to int) or itos (int to string) methods. 


In [0]:
print(text.vocab.itos[:10])
print(label.vocab.stoi)

['<unk>', '<pad>', 'the', ',', '.', 'a', 'and', 'of', 'to', 'is']
defaultdict(<function _default_unk_index at 0x7fca87925c80>, {'neg': 0, 'pos': 1})


Use **BuketIterator** to return batches of similar length sentences. 

In [0]:
batch_size = 64

device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')

train_iterator, valid_iterator, test_iterator = data.BucketIterator.splits(
    (training_data, validation_data, testing_data), 
    batch_size = batch_size,
    device = device)

### Define model
**Word Embeddings**
+ learned representaton of words
+ similar meaning - similar representation
+ dense
+ low dimensional representation


**Embedding layer** transforms sparse one-hot vector into a dense embedding vector.


![alt text](2.png)



In [0]:
import torch.nn as nn

class RNN(nn.Module):
    def __init__(self, input_dim, embedding_dim, hidden_dim, output_dim):        
        super().__init__()        
        self.embedding = nn.Embedding(input_dim, embedding_dim)        
        self.rnn = nn.RNN(embedding_dim, hidden_dim)        
        self.fc = nn.Linear(hidden_dim, output_dim)
        
    def forward(self, text):
        #text = [sent len, batch size]   
        # one-hot vector (indices of non zero values)
        embedded = self.embedding(text)        
        #embedded = [sent len, batch size, emb dim], dense vectors
        # rnn takes first hidden state initialize with zeros (by default)
        output, hidden = self.rnn(embedded)        
        #output = [sent len, batch size, hid dim]
        #hidden = [1, batch size, hid dim]   
        assert torch.equal(output[-1,:,:], hidden.squeeze(0)) 
        out = self.fc(hidden.squeeze(0))
        return out

In [0]:
input_dim = len(text.vocab)
embedding_dim = 100
hidden_dim = 256
output_dim = 1

model = RNN(input_dim, embedding_dim, hidden_dim, output_dim)

In [0]:
def count_parameters(model):
    return sum(p.numel() for p in model.parameters() if p.requires_grad)
print('Trainable parameters: ', count_parameters(model))

Trainable parameters:  2592105


In [ ]:
# return accuracy per batch, 8/10 return 0.8
def binary_accuracy(preds, y):  
    rounded_preds = torch.round(torch.sigmoid(preds))
    correct = (rounded_preds == y).float() 
    acc = correct.sum() / len(correct)
    return acc

### Define optimizer

In [0]:
import torch.optim as optim

optimizer = optim.SGD(model.parameters(), lr=1e-3)
criterion = nn.BCEWithLogitsLoss()
model = model.to(device)
criterion = criterion.to(device)

In [0]:
def train(model, iterator, optimizer, criterion):
    
    epoch_loss = 0
    epoch_acc = 0
    
    model.train()
    
    for batch in iterator:           
        optimizer.zero_grad()            
        predictions = model(batch.text).squeeze(1)        
        loss = criterion(predictions, batch.label)        
        acc = binary_accuracy(predictions, batch.label)        
        loss.backward()        
        optimizer.step()        
        epoch_loss += loss.item()
        epoch_acc += acc.item()
        
    return epoch_loss / len(iterator), epoch_acc / len(iterator)

In [0]:
def evaluate(model, iterator, criterion):
    
    epoch_loss = 0
    epoch_acc = 0
    
    model.eval()
    
    with torch.no_grad():    
        for batch in iterator:
            predictions = model(batch.text).squeeze(1)            
            loss = criterion(predictions, batch.label)            
            acc = binary_accuracy(predictions, batch.label)
            epoch_loss += loss.item()
            epoch_acc += acc.item()
        
    return epoch_loss / len(iterator), epoch_acc / len(iterator)

In [0]:
import time

def epoch_time(start_time, end_time):
    elapsed_time = end_time - start_time
    elapsed_mins = int(elapsed_time / 60)
    elapsed_secs = int(elapsed_time - (elapsed_mins * 60))
    return elapsed_mins, elapsed_secs

In [0]:
epochs = 5

best_valid_loss = 0
for epoch in range(epochs):    
    start_time = time.time()     
    train_loss, train_acc = train(model, train_iterator, optimizer, criterion)
    valid_loss, valid_acc = evaluate(model, valid_iterator, criterion)    
    end_time = time.time()
    epoch_mins, epoch_secs = epoch_time(start_time, end_time)
    
    if valid_loss < best_valid_loss:
        best_valid_loss = valid_loss
        #torch.save(model.state_dict(), 'model.pt')
    
    print(f'Epoch: {epoch+1:02} | Epoch Time: {epoch_mins}m {epoch_secs}s')
    print(f'\tTrain Loss: {train_loss:.3f} | Train Acc: {train_acc*100:.2f}%')
    print(f'\t Val. Loss: {valid_loss:.3f} |  Val. Acc: {valid_acc*100:.2f}%')

Epoch: 01 | Epoch Time: 0m 14s
	Train Loss: 0.694 | Train Acc: 50.33%
	 Val. Loss: 0.698 |  Val. Acc: 49.19%
Epoch: 02 | Epoch Time: 0m 13s
	Train Loss: 0.693 | Train Acc: 49.62%
	 Val. Loss: 0.698 |  Val. Acc: 49.13%
Epoch: 03 | Epoch Time: 0m 14s
	Train Loss: 0.693 | Train Acc: 50.09%
	 Val. Loss: 0.698 |  Val. Acc: 50.36%
Epoch: 04 | Epoch Time: 0m 14s
	Train Loss: 0.693 | Train Acc: 49.56%
	 Val. Loss: 0.698 |  Val. Acc: 49.02%
Epoch: 05 | Epoch Time: 0m 13s
	Train Loss: 0.693 | Train Acc: 50.00%
	 Val. Loss: 0.698 |  Val. Acc: 50.55%


In [0]:
#model.load_state_dict(torch.load('model.pt'))
test_loss, test_acc = evaluate(model, test_iterator, criterion)
print(f'Test Loss: {test_loss:.3f} | Test Acc: {test_acc*100:.2f}%')

Test Loss: 0.715 | Test Acc: 45.90%
